## A basic S.I.R model for Covid Situation in Bangalore 

### Flattening the curve ? Infection is peaking ? Have you wondered what that actually means ? 
This notebook is an attempt to simplify and help understand how to model a pandemic using S.I.R Model(Suseptible,Infected,Recovered).The predicted statistics from the notebook maybe inaccurate with real life observations but the intention of this notebook is to convey how avaiable data can be used for the purpose.

This notebook comprises of the 3 main parts:
    1. Data clean-up and extrapolation
    2. SIR Model
    3. Plotting using KeplerGL

## 1. Data Clean-up 

In [1]:
import pandas as pd
import numpy as np

<p> The below file consists of ward-wise data about the containtement zone and its severity as of early late-April/early-May,2020.<br> Any graph showing day-0,day-1...day-n and so on can be inffered to approximately May 1st +n days
</p>

In [2]:
df=pd.read_csv('BBMP.csv')

In [3]:
df.dropna(inplace=True) #Has a couple of rows containing na values which we can remove 
df.head()

Ward Number       Ward Name          Zone Assembly Constituency Covid Zone  \
0        135.0  Padarayanapura          West             Chamajpet        Red   
1        189.0     Hongasandra  Bommanahalli          Bommanahalli        Red   
2         93.0   Vasanth Nagar          East          Shivajinagar     Orange   
3        133.0     Hampinagara         South           Vijayanagar     Orange   
4        134.0    Bapuji Nagar         South           Vijayanagar     Orange   

  Containment Zone  
0              Yes  
1              Yes  
2              Yes  
3              Yes  
4              Yes

### Convert the ward numbers to integers instead of float

In [4]:
data=df
data['Ward Number']=data['Ward Number'].astype('int64') 

In [5]:
data.set_index('Ward Number',inplace=True)
data.sort_index(inplace=True)
data.head() # Now we have a cleaner representation

Ward Name       Zone Assembly Constituency  \
Ward Number                                                            
1                        Kempegowda  Yelahanka             Yelahanka   
2                      Chowdeshwari  Yelahanka             Yelahanka   
3                            Atturu  Yelahanka             Yelahanka   
4            Yelahanka Satellite To  Yelahanka             Yelahanka   
5                           Jakkuru  Yelahanka        Bytarayanapura   

            Covid Zone Containment Zone  
Ward Number                              
1                Green               No  
2                Green               No  
3                Green               No  
4                Green               No  
5                Green               No


### Now that I have a list of all the places and their status , I would also like to know details about each of these wards/sectors.  I was able to find census data on a gov website which could aid me in this.This data is stored in cencus.csv file. 


In [6]:
# Lets import the data and perform a little cleanup before we use it 
census=pd.read_csv('cencus.csv',names=['ward_no', 'representative', 'female', 'population', 'category', 'area',
       'Ward Name', 'st', 'localities', 'sc', 'constituency', 'male'])
census.drop(0,inplace=True)
census['ward_no']=census['ward_no'].astype('int64') 

In [7]:
census.head()

ward_no                representative female population  \
1      147  S.M.Murugesh Modaliyar (INC)  14269      29945   
2      114                  Sarala (INC)  15524      35632   
3      105              Roopa Devi (BJP)  12716      26857   
4       56              S.S.Prasad (BJP)  14014      29420   
5      196             S.Gangadhar (INC)  10293      21080   

                      category   area             Ward Name   st  \
1                      General    1.6               Adugodi  411   
2              Scheduled Caste  11.26                Agaram  167   
3  Backward Category A (Women)    0.8  Agrahara Dasarahalli  433   
4          Backward Category A   2.15        A Narayanapura  118   
5                      General  11.92            Anjanapura  226   

                                          localities     sc     constituency  \
1  ['Rajendra Nagar', ' Rajendra Nagar slum', ' V...   5381     B T M Layout   
2  ['Cambridge layout', ' Jeevan Kendra Layout', ...  12434     Shanthinagar   
3  ['Indira Colony', ' West of Chord road 4th Sta...   3172   Govindrajnagar   
4  ['Jyothipuram', ' Mahadevapura', ' A Narayanpu...   5827        K R Puram   
5  ['Soudhamini Layout', ' Muneshwar Nagar', ' Av...   2671  Bangalore South   

    male  
1  15676  
2  20108  
3  14141  
4  15406  
5  10787

In [8]:
# Lets pick a few useful columns for now
census=census[['area', 'ward_no', 'male','female','population']]
census.head()

area  ward_no   male female population
1    1.6      147  15676  14269      29945
2  11.26      114  20108  15524      35632
3    0.8      105  14141  12716      26857
4   2.15       56  15406  14014      29420
5  11.92      196  10787  10293      21080

In [9]:
#great now we have some background data about each ward to work with
census.set_index('ward_no',inplace=True)
census.sort_index(inplace=True)
census.head()

area   male female population
ward_no                                
1        10.47  11490  10376      21866
2         7.06  10402   9224      19626
3        10.15  13129  10891      24020
4          4.9  13457  12325      25782
5        23.96  10906  10058      20964

In [10]:
#now that we have both the dataframes clean and indexed lets join them
all_data=data.join(census)
all_data

Ward Name          Zone Assembly Constituency  \
Ward Number                                                               
1                        Kempegowda     Yelahanka             Yelahanka   
2                      Chowdeshwari     Yelahanka             Yelahanka   
3                            Atturu     Yelahanka             Yelahanka   
4            Yelahanka Satellite To     Yelahanka             Yelahanka   
5                           Jakkuru     Yelahanka        Bytarayanapura   
...                             ...           ...                   ...   
194                       Gottigere  Bommanahalli       Bangalore South   
195                     Konanakunte  Bommanahalli       Bangalore South   
196                      Anjanapura  Bommanahalli       Bangalore South   
197                     Vasanthpura  Bommanahalli       Bangalore South   
198                     Hemmigepura      RR Nagar          Yeshwanthpur   

            Covid Zone Containment Zone   area   male female population  
Ward Number                                                              
1                Green               No  10.47  11490  10376      21866  
2                Green               No   7.06  10402   9224      19626  
3                Green               No  10.15  13129  10891      24020  
4                Green               No    4.9  13457  12325      25782  
5                Green               No  23.96  10906  10058      20964  
...                ...              ...    ...    ...    ...        ...  
194              Green               No   6.49  11402  10124      21526  
195              Green               No   3.42  10662   9519      20181  
196              Green               No  11.92  10787  10293      21080  
197              Green               No   5.34  13057  11465      24522  
198              Green               No  28.59  12926  11385      24311  

[198 rows x 9 columns]

#### Let's export and save this dataframe 

In [11]:
all_data.to_csv('all_data.csv')

### The all_data dataframe contains a varity of information which we can use in different ways

    There may be a number ways to model this more accurately but here I'm going to take a simplistic approach.
    Let's say the infection rate in a ward can be represent by the below equations,

    Lets give numerical representation to the categorical values in Covid and containment zone columns.


In [12]:
# Explain the mapping
Zone_map={"Green":2,"Yellow":5,"Orange":7,"Red":10,"Yes":5,"No":1}

In [13]:
#We can apply this mapping to the above df by using dfreplace
data=all_data.replace(Zone_map)
data.head()

Ward Name       Zone Assembly Constituency  \
Ward Number                                                            
1                        Kempegowda  Yelahanka             Yelahanka   
2                      Chowdeshwari  Yelahanka             Yelahanka   
3                            Atturu  Yelahanka             Yelahanka   
4            Yelahanka Satellite To  Yelahanka             Yelahanka   
5                           Jakkuru  Yelahanka        Bytarayanapura   

             Covid Zone  Containment Zone   area   male female population  
Ward Number                                                                
1                     2                 1  10.47  11490  10376      21866  
2                     2                 1   7.06  10402   9224      19626  
3                     2                 1  10.15  13129  10891      24020  
4                     2                 1    4.9  13457  12325      25782  
5                     2                 1  23.96  10906  10058      20964

# The S.I.R Model
Compartmental models simplify the mathematical modelling of infectious diseases. The population is assigned to compartments with labels - for example, S, I, or R. People may progress between compartments, like the suseptible may get infected or the infected may eventually recover etc.

In [14]:
#Initially everyone would be susceptible
data['susceptible']=data['population']

In [15]:
# We start with a probability of having an infection which can be a product of a rand and area of the ward
# considering the fact that covid spreads faster in densely populated areas.
data['infected']=np.random.rand(len(data)) * data['area'].astype('float32')

In [16]:
#Then we normalize to a value bw 0-1 , if real data is available it can be plugged in here 
data['infected']=(data['infected']-data['infected'].min())/(data['infected'].max()-data['infected'].mean())

In [17]:
#And number of recovered would be 0
data['recovered']=0

In [18]:
data

Ward Name          Zone Assembly Constituency  \
Ward Number                                                               
1                        Kempegowda     Yelahanka             Yelahanka   
2                      Chowdeshwari     Yelahanka             Yelahanka   
3                            Atturu     Yelahanka             Yelahanka   
4            Yelahanka Satellite To     Yelahanka             Yelahanka   
5                           Jakkuru     Yelahanka        Bytarayanapura   
...                             ...           ...                   ...   
194                       Gottigere  Bommanahalli       Bangalore South   
195                     Konanakunte  Bommanahalli       Bangalore South   
196                      Anjanapura  Bommanahalli       Bangalore South   
197                     Vasanthpura  Bommanahalli       Bangalore South   
198                     Hemmigepura      RR Nagar          Yeshwanthpur   

             Covid Zone  Containment Zone   area   male female population  \
Ward Number                                                                 
1                     2                 1  10.47  11490  10376      21866   
2                     2                 1   7.06  10402   9224      19626   
3                     2                 1  10.15  13129  10891      24020   
4                     2                 1    4.9  13457  12325      25782   
5                     2                 1  23.96  10906  10058      20964   
...                 ...               ...    ...    ...    ...        ...   
194                   2                 1   6.49  11402  10124      21526   
195                   2                 1   3.42  10662   9519      20181   
196                   2                 1  11.92  10787  10293      21080   
197                   2                 1   5.34  13057  11465      24522   
198                   2                 1  28.59  12926  11385      24311   

            susceptible  infected  recovered  
Ward Number                                   
1                 21866  0.000876          0  
2                 19626  0.000402          0  
3                 24020  0.000616          0  
4                 25782  0.000012          0  
5                 20964  0.002538          0  
...                 ...       ...        ...  
194               21526  0.000672          0  
195               20181  0.000065          0  
196               21080  0.000179          0  
197               24522  0.000536          0  
198               24311  0.001305          0  

[198 rows x 12 columns]

### Why is the infected a floating point value ?
It can be thought of as the initial probability of occurance of the 1st infection in that ward.

### Equations for modeling each compartment 
![title](https://wikimedia.org/api/rest_v1/media/math/render/svg/29728a7d4bebe8197dca7d873d81b9dce954522e)

Here dS represnt the rate of change in the population that is suseptible and it is characterized by count(Infected) represented by I , count(Suseptible) represented by S and N the total population count.
Similarly we use these to model dI the rate of change in infected population as well as dR the rate of change in recovered population. 


The Greek alphabets here can be thought of as scaling factors and are represented in this notebook as const_a and const_b(for beta) and const_r(for gamma). You can read more about this and how infection rate is calculated from [here](https://en.wikipedia.org/wiki/Compartmental_models_in_epidemiology)


In [19]:
#CONSTANT a --> rate of infection
#const_a

#CONSTANT b --> Rate of reduction of infected people
#const_b

#CONSTANT r --> Recovery Rate
#const_r

In [20]:
# Population = S(t) + I(t) + R(t)
# Now we need to calculate the rate of change each col in (S,I,R) wrt time/

In [21]:
#Feel free to change up these values and observe how the graph changes 
#CONSTANT a --> rate of infection
a=1.6247 
#CONSTANT b --> Rate of reduction of infected people
b=0.014286
#CONSTANT r --> Recovery Rate
r=0.3

In [22]:
def delta_S(S,I,const_a=a): 
    # here I= I[t-1] cause new susceptible number will be wrt prev infected count
    return -const_a * S * I


In [23]:
#delta_I = no of infected at time t, given by --> (const_a * S) - (const_b * I)
# whoever were susceptible and got infected are transfered from S to I
# but also there are people who are constantly out of I state,i.e-> recover or pass_away, that is captured by const_b
def delta_I(I,S,const_a=a,const_b=b):
    return  (const_a * S * I) - (const_b * I)

In [24]:
# Rate of recovery
def delta_R(I,const_r=b):
    return const_r*I

In [25]:
data[['susceptible','infected','recovered']]=data[['susceptible','infected','recovered']].astype('float32')

In [26]:
for c in data.columns:
    print(c,' -- ',data[c].dtype)

Ward Name  --  object
Zone  --  object
Assembly Constituency  --  object
Covid Zone  --  int64
Containment Zone  --  int64
area  --  object
male  --  object
female  --  object
population  --  object
susceptible  --  float32
infected  --  float32
recovered  --  float32


### Lets test out these equations for few ward's   

In [27]:
d=data.sample(frac=0.05)
wards=d.values.tolist()
d

Ward Name      Zone Assembly Constituency  Covid Zone  \
Ward Number                                                                  
123               Vijayanagara     South           Vijayanagar           2   
146                Lakkasandra     South          B.T.M Layout           2   
57              Cv Raman Nagar      East        C.V.Ramannagar           2   
165            Ganesh Mandiara     South       Padmanabhanagar           2   
130                     Ullalu  RR Nagar          Yeshwanthpur           2   
162                  Girinagar     South       Padmanabhanagar           2   
45                 Malleswaram      West          Malleshwaram           2   
153                 Jayanagara     South               Chikpet           2   
73                Kottegepalya  RR Nagar    Rajarajeswarinagar           2   
74           Shakthi Ganapathi      West    Mahalakshmi Layout           2   

             Containment Zone  area   male female population  susceptible  \
Ward Number                                                                 
123                         1  0.73  19009  17068      36077      36077.0   
146                         1  1.29  14909  13394      28303      28303.0   
57                          1  3.58  15822  13938      29760      29760.0   
165                         1  1.63  11988  11113      23101      23101.0   
130                         1  8.92  10468   9864      20332      20332.0   
162                         1  1.77  18208  16704      34912      34912.0   
45                          1  1.81  18994  17327      36321      36321.0   
153                         1   2.5  18173  17790      35963      35963.0   
73                          1  5.84  15812  13288      29100      29100.0   
74                          1   0.7  17953  16577      34530      34530.0   

             infected  recovered  
Ward Number                       
123          0.000033        0.0  
146          0.000041        0.0  
57           0.000174        0.0  
165          0.000026        0.0  
130          0.000596        0.0  
162          0.000057        0.0  
45           0.000036        0.0  
153          0.000202        0.0  
73           0.000350        0.0  
74           0.000049        0.0

In [28]:
#Example data to refer for below
wards[0]

['Vijayanagara',
 'South',
 'Vijayanagar',
 2,
 1,
 '0.73',
 '19009',
 '17068',
 '36077',
 36077.0,
 3.259263394284062e-05,
 0.0]

In [29]:
#Let us setup a time-frame to model the spread 
days=90

In [30]:
def get_deltas_for_ward(ward,const_a= 0.00001,const_b=0.0000021,const_r=0.003,days=25):
    log=[ward]#[[ward[-1],ward[-2],ward[-3]]]
    delta_log=[]
    
    for day in range(0,days):
        d_s=delta_S(log[day][-3],log[day-1][-2],const_a = 0.00001) 
        d_i=delta_I(log[day][-2],log[day][-3] ,const_a=0.00001,const_b=0.0000021) 
        d_r=delta_R(log[day][-2],const_r=0.003)
        
        log.append([ log[day][-3] + d_s if log[day][-3] + d_s >= 0 else 0 ,
                    log[day][-2] + d_i if log[day][-2] + d_i >= 0 else 0,
                    log[day][-1] + d_r])
        
        delta_log.append([d_s,d_i,d_r])
        
    return delta_log,log

In [31]:
#Here we will store only the delta i.e the rate of change/spread for each data of each ward hence we use _  
ward_wise=[]
for ward in wards:
    dat,_=get_deltas_for_ward(ward,days=days)
    ward_wise.append(dat)

In [32]:
# we will recast this into a numpy array for now
dat=np.array(ward_wise)
# shape ==> (no_of_wards,no_of_days,SIR_values)
dat.shape

(10, 90, 3)

Here let's plot all the 3 parameters: 

In [33]:
import plotly.graph_objects as go
fig = go.Figure()
for wa in range(len(ward_wise)):
    #Infection rate - RED LINE
    fig.add_trace(go.Scatter(y=dat[wa][:,1],
                    mode='lines',
                    name='lines',line={"color":'red'}))
    #Sus rate - ORANGE LINE
    fig.add_trace(go.Scatter(y=dat[wa][:,0],
                    mode='lines',
                    name='lines',line={"dash":'dot','color':'orange'}))
    #Recovered rate - GREEN LINE
    fig.add_trace(go.Scatter(y=dat[wa][:,2],
                    mode='lines',
                    name='lines',line={"dash":'dashdot','color':'green'},fill='toself'))

In [34]:
fig.show()

You maybe consufed as to why we have a distribution on the -ve region , that is because we are only plotting the change per unit time of the quantity and as expect the number of suseptible people keep reducing at an increaring rate as the infection spreads , the suspetable people are transffered to infected category.

## Cleaning it up a bit and computing for all the wards

In [35]:
d=data
wards=d.values.tolist()
days=140 #change if needed
ward_wise=[]
for ward in wards:
    dat,_=get_deltas_for_ward(ward,days=days)
    ward_wise.append(dat)

In [36]:
dat=np.array(ward_wise)
dat.shape

(198, 140, 3)

In [37]:
fig = go.Figure()
for wa in range(len(ward_wise)):
    fig.add_trace(go.Scatter(y=dat[wa][:,1],
                    mode='lines'))

In [38]:
fig.show()

In [39]:
#Lets save this to for reference , uncomment the below line
#fig.write_html('plot.html')

# As we can see the above image is missing a lot of details that we maybe expecting to see such as the ward name etc . Lets add the details now

Remeber that these graphs that are generated are interactive plotly graphs , you may hover over them to see data , click on legend elements to isolate them on the display and more. Do check them out.

In [40]:
fig = go.Figure()
for wa in range(len(ward_wise)):
    fig.add_trace(go.Scatter(y=dat[wa][:,1],
                    mode='lines',
                    name='infection'+" "+wards[wa][0]+" "+wards[wa][1]))
    fig.add_trace(go.Scatter(y=dat[wa][:,2],
                    mode='markers', name='recovery'+ " " + wards[wa][0]+" "+wards[wa][1]))

In [41]:
#Be sure to use the interactive features of the plot by hovering, clicking on a legend item, zoom, pan etc.
fig.show()

## Now here on lets pick one attribute , the Infection Rate , to plot as we have seen it can get real messy

In [42]:
d=data.sort_values(by="Ward Number")
wards=d.values.tolist()

days=100  #Change if needed

ward_wise_inf=[]
for ward in wards:
    dat,_=get_deltas_for_ward(ward,days=days)
    ward_wise_inf.append(np.array(dat)[:,1])

In [43]:
ward_wise_inf=np.array(ward_wise_inf)
ward_wise_inf.shape

(198, 100)

In [44]:
time_series=pd.DataFrame(ward_wise_inf,index=list(range(1,199)))

In [45]:
# Here we have a time-series representation of the data where the rows represent the WARDNUMBERS and columns are days
time_series.head()

0         1         2         3         4         5         6   \
1  0.000192  0.000233  0.000285  0.000347  0.000423  0.000515  0.000628   
2  0.000079  0.000094  0.000113  0.000135  0.000161  0.000193  0.000231   
3  0.000148  0.000183  0.000227  0.000282  0.000350  0.000434  0.000538   
4  0.000003  0.000004  0.000005  0.000006  0.000008  0.000010  0.000012   
5  0.000532  0.000644  0.000778  0.000942  0.001139  0.001378  0.001667   

         7         8         9   ...           90           91           92  \
1  0.000765  0.000932  0.001136  ...  1138.699171  1009.553820   872.845978   
2  0.000276  0.000331  0.000396  ...   588.601378   665.801006   745.889745   
3  0.000667  0.000827  0.001026  ...   497.188818   382.065166   289.731542   
4  0.000015  0.000019  0.000024  ...  1608.728427  1776.268485  1909.421303   
5  0.002016  0.002439  0.002950  ...   776.055644   659.040258   549.590535   

            93           94           95           96           97  \
1   737.474173   610.438241   496.355165   397.533509   314.411434   
2   826.431376   904.257442   975.552511  1036.073177  1081.515041   
3   217.440539   161.884479   119.789953    88.233960    64.766183   
4  1990.813664  2006.152919  1948.122608  1819.305809  1632.669165   
5   451.125984   365.344441   292.556968   232.106966   182.765367   

            98           99  
1   246.134753   191.105793  
2  1108.007903  1112.674001  
3    47.416598    34.646149  
4  1408.959852  1171.810693  
5   143.045043   111.419557  

[5 rows x 100 columns]

In [46]:
#time_series.to_csv('TS.csv')

## Now let us try combine this with geographical data and plot it on a map 
 We'll be using GeoJSON data of Bangalore and we will also be plotting the geo+stat data onto a map using keplerGL.

In [47]:
with open('BBMP.GeoJSON', 'r') as f:
    geojson = f.read()

In [48]:
# Pandas wrapper for handeling geograhical data 
import geopandas as gpd

In [49]:
gdf=gpd.read_file('BBMP.GeoJSON')
gdf.head(2)

OBJECTID ASS_CONST_ ASS_CONST1  WARD_NO         WARD_NAME    POP_M  \
0         1        150  Yelahanka      2.0  Chowdeswari Ward  10402.0   
1         2        150  Yelahanka      3.0            Atturu  13129.0   

     POP_F  POP_SC  POP_ST  POP_TOTAL  AREA_SQ_KM        LAT        LON  \
0   9224.0  2630.0   286.0    19626.0        7.06  13.121709  77.580422   
1  10891.0  2921.0   665.0    24020.0       10.15  13.102805  77.560038   

        RESERVATIO                                           geometry  
0          General  MULTIPOLYGON (((77.59229 13.09720, 77.59094 13...  
1  General (Women)  MULTIPOLYGON (((77.56862 13.12705, 77.57064 13...

In [50]:
# Converting and setting the the WARD_NO as the row index as it will be easier to join the dataframe with our timeseries data
gdf['WARD_NO']=gdf['WARD_NO'].astype(int)

In [51]:
gdf.set_index('WARD_NO',inplace=True)

In [52]:
gdf.sort_index(inplace=True)
gdf.head(2)

OBJECTID ASS_CONST_ ASS_CONST1         WARD_NAME    POP_M    POP_F  \
WARD_NO                                                                       
1             186        150  Yelahanka   Kempegowda Ward  11490.0  10376.0   
2               1        150  Yelahanka  Chowdeswari Ward  10402.0   9224.0   

         POP_SC  POP_ST  POP_TOTAL  AREA_SQ_KM        LAT        LON  \
WARD_NO                                                                
1        1912.0   430.0    21866.0       10.47  13.116188  77.599713   
2        2630.0   286.0    19626.0        7.06  13.121709  77.580422   

                    RESERVATIO  \
WARD_NO                          
1        Backward Category - B   
2                      General   

                                                  geometry  
WARD_NO                                                     
1        MULTIPOLYGON (((77.61515 13.13117, 77.61494 13...  
2        MULTIPOLYGON (((77.59229 13.09720, 77.59094 13...

### Joining the geo and statistical data

In [53]:
final=gpd.GeoDataFrame(time_series[[2]].join(gdf['geometry']))
final.columns=["data","geometry"]

### Using KeplerGL 

In [54]:
import keplergl

In [64]:
#Add the data containing the geo-info first
map_1 = keplergl.KeplerGl(height=600)
map_1.add_data(geojson,"geodata")

User Guide: https://github.com/keplergl/kepler.gl/blob/master/docs/keplergl-jupyter/user-guide.md


In [65]:
# After running this cell you will find a html file named "infection_map in cwd.
# Open it in the web browser to see the data visualization
map_1.save_to_html(file_name="infection_map.html")

Map saved to infection_map.html!


In [66]:
from IPython.display import IFrame

IFrame(src='infection_map.html',width=700, height=600)

In [67]:
#Now lets add the infection data onto the map

In [88]:
#Here is a small helper class which will generate an output map view for any given day
# Note here day 0 is considered as some day in early May of 2020
class Covid_Mapper():
    
    def __init__(self,filename="kepler_infection_map.html"):
        with open('BBMP.GeoJSON', 'r') as f:
            self.geojson = f.read()
            
        #The follow is all the csv file which are stored representations of dataframe
        # Be sure to uncomment .to_csv() int the cells above incase you are missing any of these files.
        self.time_series=pd.read_csv('TS.csv',index_col="Unnamed: 0")
        self.gdf=gpd.read_file('BBMP.GeoJSON')
        self.gdf['WARD_NO']=self.gdf['WARD_NO'].astype(int)
        self.gdf.set_index('WARD_NO',inplace=True)
        self.gdf.sort_index(inplace=True)
        self.filename = filename
    
    def get_for_day(self,day):
        day=str(day)
        final=gpd.GeoDataFrame(self.time_series[[day]].join(self.gdf[['LAT','LON','geometry']]))
        final.columns=["data","Lat","Lon","geometry"]
        map_1 = keplergl.KeplerGl(height=600)
        map_1.add_data(self.geojson,"geoj")
        map_1.add_data(final,name='final')
        map_1.save_to_html(file_name=self.filename)

#### In the below cell, the helper class is instantiated and the day number for which the map plot is to be generated is passed as the "day" parameter to the get_for_day method. 

In [85]:
#Running this cell will automatically over-write any old file named "kepler_infection_map.html"
covid_map=Covid_Mapper()
covid_map.get_for_day(day=50)

User Guide: https://github.com/keplergl/kepler.gl/blob/master/docs/keplergl-jupyter/user-guide.md
Map saved to kepler_infection_map.html!


### At the time of making this notebook I couldnt find a way to preset the map setting.
### Please follow the below instructions to color the map after running the following cell :
1. Click on the arrow at the top-left of the map screen  
2. Select the 'geoj' tab and disable the "Fill Color" toggle button
3. Select the 'final' tab, in Fill Color and click on the select 3-bot-button beside the toggle button
4. Click on the "Color Based On" Field and set it to data.
<br><br>
The map should now be color as per the covid-data for that day
<p>NOTE : By default the map-colors are inverted, that is , darker=less,to invert it you can select the color bar below fill color and select an appropriate pallet.</p>

In [87]:
IFrame(src='kepler_infection_map.html',width=700, height=600)

# END